In [1]:
import numpy as np
import pandas as pd
import os
import librosa
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from imblearn.over_sampling import RandomOverSampler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, Dropout
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping

# CSV 파일에서 오디오 파일 경로 및 레이블 읽기
train_df = pd.read_csv('train.csv')
test_df = pd.read_csv('test.csv')

data = []
labels = []

# 훈련 데이터 처리
for index, row in tqdm(train_df.iterrows(), total=len(train_df)):
    file_path = row['path']  # CSV 파일의 경로 열 이름에 맞게 조정
    label = row['label']  # CSV 파일의 레이블 열 이름에 맞게 조정

    audio, sample_rate = librosa.load(file_path, res_type="kaiser_fast")
    mfccs_features = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40)
    mfccs_features_scaled = np.mean(mfccs_features.T, axis=0)
    data.append(mfccs_features_scaled)
    labels.append(label)

# Unlabeled 데이터 처리
unlabeled_data_dir = 'unlabeled_data'
for root, dirs, files in os.walk(unlabeled_data_dir):
    for file in files:
        file_path = os.path.join(root, file)
        audio, sample_rate = librosa.load(file_path, res_type="kaiser_fast")
        mfccs_features = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40)
        mfccs_features_scaled = np.mean(mfccs_features.T, axis=0)
        data.append(mfccs_features_scaled)
        labels.append('unknown')  # 레이블 없는 데이터

# Feature DataFrame 생성
feature_df = pd.DataFrame({"features": data, "class": labels})

# 레이블 인코딩
def label_encoder(column):
    le = LabelEncoder().fit(column)
    print(column.name, le.classes_)
    return le.transform(column)

feature_df["class"] = label_encoder(feature_df["class"])

X = np.array(feature_df["features"].tolist())
y = np.array(feature_df["class"].tolist())

# 데이터 균형 맞추기
ros = RandomOverSampler(random_state=42)
X_resampled, y_resampled = ros.fit_resample(X, y)

y_resampled = to_categorical(y_resampled)

X_train, X_val, y_train, y_val = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

num_labels = len(feature_df["class"].unique())

input_shape = (X.shape[1],)

# 모델 생성 (TensorFlow를 사용하는 예시이므로 PyTorch로 변환해야 할 수 있음)
model = Sequential()
model.add(Dense(128, input_shape=input_shape))
model.add(Activation(activation="relu"))
model.add(Dropout(0.5))
model.add(Dense(256))
model.add(Activation(activation="relu"))
model.add(Dropout(0.5))
model.add(Dense(128))
model.add(Activation(activation="relu"))
model.add(Dropout(0.5))
model.add(Dense(num_labels))
model.add(Activation(activation="softmax"))

model.compile(loss="categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

model.summary()

early = EarlyStopping(monitor="val_loss", patience=5)

history = model.fit(X_train, y_train, validation_data=(X_val, y_val), batch_size=2, epochs=100, callbacks=[early])

val_loss, val_acc = model.evaluate(X_val, y_val)
print("Validation Loss:", val_loss)
print("Validation Accuracy:", val_acc)

# 테스트 데이터 예측 및 제출 파일 생성
def detect_fake(filename):
    sound_signal, sample_rate = librosa.load(filename, res_type="kaiser_fast")
    mfcc_features = librosa.feature.mfcc(y=sound_signal, sr=sample_rate, n_mfcc=40)
    mfccs_features_scaled = np.mean(mfcc_features.T, axis=0)
    mfccs_features_scaled = mfccs_features_scaled.reshape(1, -1)
    result_array = model.predict(mfccs_features_scaled)
    
    # Debug prints
    print("Result Array Shape:", result_array.shape)
    print("Result Array Values:", result_array)
    
    if result_array.shape[1] != 2:
        print("Warning: Unexpected result array shape")
        return "UNKNOWN"

    result_classes = ["FAKE", "REAL"]
    result = np.argmax(result_array[0])
    
    print("Argmax Result:", result)
    
    return result_classes[result]

# 예측 함수를 사용하여 각 파일에 대한 예측 결과 리스트 생성
predictions = []
for index, row in tqdm(test_df.iterrows(), total=len(test_df)):
    file_path = row['path']  # CSV 파일의 경로 열 이름에 맞게 조정
    prediction = detect_fake(file_path)
    predictions.append(prediction)

# 예측 결과를 DataFrame으로 만들어 CSV 파일로 저장
submit = pd.read_csv('./sample_submission.csv')
submit.iloc[:, 1] = predictions
submit.to_csv('./sg_submit3.csv', index=False)

# baseline_submit.csv 파일이 생성되었음을 알림
print("sg_submit3.csv 파일이 생성되었습니다.")


100%|██████████| 55438/55438 [30:57<00:00, 29.84it/s]


class ['fake' 'real' 'unknown']


c:\Users\moon0\anaconda3\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense (Dense)                   │ (None, 128)            │         5,248 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation (Activation)         │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 256)            │        33,024 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_1 (Activation)       │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_2 (Activation)       │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 3)              │           387 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_3 (Activation)       │ (None, 3)              │             0 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

...

 19%|█▊        | 9309/50000 [34:37<2:42:47,  4.17it/s]

Result Array Shape: (1, 3)
Result Array Values: [[0. 0. 1.]]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step


 19%|█▊        | 9310/50000 [34:37<2:31:20,  4.48it/s]

Result Array Shape: (1, 3)
Result Array Values: [[0. 0. 1.]]


KeyboardInterrupt: 

In [1]:
import numpy as np
import pandas as pd
import os
import librosa
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from imblearn.over_sampling import RandomOverSampler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, Dropout
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping

# CSV 파일에서 오디오 파일 경로 및 레이블 읽기
train_df = pd.read_csv('train.csv')
test_df = pd.read_csv('test.csv')

data = []
labels = []

# 훈련 데이터 처리
for index, row in tqdm(train_df.iterrows(), total=len(train_df)):
    file_path = row['path']  # CSV 파일의 경로 열 이름에 맞게 조정
    label = row['label']  # CSV 파일의 레이블 열 이름에 맞게 조정

    audio, sample_rate = librosa.load(file_path, res_type="kaiser_fast")
    mfccs_features = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40)
    mfccs_features_scaled = np.mean(mfccs_features.T, axis=0)
    data.append(mfccs_features_scaled)
    labels.append(label)

# Unlabeled 데이터 처리
unlabeled_data_dir = 'unlabeled_data'
for root, dirs, files in os.walk(unlabeled_data_dir):
    for file in files:
        file_path = os.path.join(root, file)
        audio, sample_rate = librosa.load(file_path, res_type="kaiser_fast")
        mfccs_features = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40)
        mfccs_features_scaled = np.mean(mfccs_features.T, axis=0)
        data.append(mfccs_features_scaled)
        labels.append('unknown')  # 레이블 없는 데이터

# Feature DataFrame 생성
feature_df = pd.DataFrame({"features": data, "class": labels})

# 레이블 인코딩
def label_encoder(column):
    le = LabelEncoder().fit(column)
    print(column.name, le.classes_)
    return le.transform(column)

feature_df["class"] = label_encoder(feature_df["class"])

X = np.array(feature_df["features"].tolist())
y = np.array(feature_df["class"].tolist())

# 데이터 균형 맞추기
ros = RandomOverSampler(random_state=42)
X_resampled, y_resampled = ros.fit_resample(X, y)

y_resampled = to_categorical(y_resampled)

X_train, X_val, y_train, y_val = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

num_labels = len(feature_df["class"].unique())

input_shape = (X.shape[1],)

# 모델 생성 (TensorFlow를 사용하는 예시이므로 PyTorch로 변환해야 할 수 있음)
model = Sequential()
model.add(Dense(256, input_shape=input_shape))
model.add(Activation(activation="relu"))
model.add(Dropout(0.5))
model.add(Dense(256))
model.add(Activation(activation="relu"))
model.add(Dropout(0.5))
model.add(Dense(128))
model.add(Activation(activation="relu"))
model.add(Dropout(0.5))
model.add(Dense(num_labels))
model.add(Activation(activation="softmax"))

model.compile(loss="categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

model.summary()

early = EarlyStopping(monitor="val_loss", patience=5)

history = model.fit(X_train, y_train, validation_data=(X_val, y_val), batch_size=2, epochs=100, callbacks=[early])

val_loss, val_acc = model.evaluate(X_val, y_val)
print("Validation Loss:", val_loss)
print("Validation Accuracy:", val_acc)

# 테스트 데이터 예측 및 제출 파일 생성
def detect_fake(filename):
    sound_signal, sample_rate = librosa.load(filename, res_type="kaiser_fast")
    mfcc_features = librosa.feature.mfcc(y=sound_signal, sr=sample_rate, n_mfcc=40)
    mfccs_features_scaled = np.mean(mfcc_features.T, axis=0)
    mfccs_features_scaled = mfccs_features_scaled.reshape(1, -1)
    result_array = model.predict(mfccs_features_scaled)
    
    # Debug prints
    print("Result Array Shape:", result_array.shape)
    print("Result Array Values:", result_array)
    
    if result_array.shape[1] != 2:
        print("Warning: Unexpected result array shape")
        return "UNKNOWN"

    result_classes = ["FAKE", "REAL"]
    result = np.argmax(result_array[0])
    
    print("Argmax Result:", result)
    
    return result_classes[result]

# 예측 함수를 사용하여 각 파일에 대한 예측 결과 리스트 생성
predictions = []
for index, row in tqdm(test_df.iterrows(), total=len(test_df)):
    file_path = row['path']  # CSV 파일의 경로 열 이름에 맞게 조정
    prediction = detect_fake(file_path)
    predictions.append(prediction)

# 예측 결과를 DataFrame으로 만들어 CSV 파일로 저장
submit = pd.read_csv('./sample_submission.csv')
submit.iloc[:, 1] = predictions
submit.to_csv('./sg_submit4csv', index=False)

# baseline_submit.csv 파일이 생성되었음을 알림
print("sg_submit4.csv 파일이 생성되었습니다.")


100%|██████████| 55438/55438 [38:00<00:00, 24.31it/s] 


class ['fake' 'real' 'unknown']


c:\Users\moon0\anaconda3\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense (Dense)                   │ (None, 256)            │        10,496 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation (Activation)         │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 256)            │        65,792 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_1 (Activation)       │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_2 (Activation)       │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 3)              │           387 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation_3 (Activation)       │ (None, 3)              │             0 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 109,571 (428.01 KB)

 Trainable params: 109,571 (428.01 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 57s 2ms/step - accuracy: 0.7772 - loss: 1.2940 - val_accuracy: 0.9533 - val_loss: 0.1584
Epoch 2/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 58s 2ms/step - accuracy: 0.9256 - loss: 0.2776 - val_accuracy: 0.9636 - val_loss: 0.1341
Epoch 3/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 57s 2ms/step - accuracy: 0.9304 - loss: 0.2739 - val_accuracy: 0.9728 - val_loss: 0.1176
Epoch 4/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 63s 2ms/step - accuracy: 0.9347 - loss: 0.2650 - val_accuracy: 0.9723 - val_loss: 0.0971
Epoch 5/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 58s 2ms/step - accuracy: 0.9379 - loss: 0.2611 - val_accuracy: 0.9711 - val_loss: 0.1289
Epoch 6/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 58s 2ms/step - accuracy: 0.9418 - loss: 0.2526 - val_accuracy: 0.9691 - val_loss: 0.1217
Epoch 7/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 62s 2ms/step - accuracy: 0.9410 - loss: 0.2582 - val_accuracy: 0.9711 - val_loss: 0.1104
Epoch 8/100
33382/33382 ━━━━━━━━━━━━━━━━━━━━ 65s 2ms/step - ac

In [2]:
import numpy as np
import pandas as pd
import os
import librosa
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from imblearn.over_sampling import RandomOverSampler
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Activation, Dropout, Add, Attention, Reshape, LayerNormalization
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping

# CSV 파일에서 오디오 파일 경로 및 레이블 읽기
train_df = pd.read_csv('train.csv')
test_df = pd.read_csv('test.csv')

data = []
labels = []

# 특징 추출 함수
def extract_features(file_path):
    audio, sample_rate = librosa.load(file_path, res_type="kaiser_fast")
    mfccs_features = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40)
    mfccs_features_scaled = np.mean(mfccs_features.T, axis=0)
    
    mel_spectrogram = librosa.feature.melspectrogram(y=audio, sr=sample_rate)
    mel_spectrogram_db = librosa.power_to_db(mel_spectrogram, ref=np.max)
    mel_spectrogram_scaled = np.mean(mel_spectrogram_db.T, axis=0)
    
    spectral_contrast = librosa.feature.spectral_contrast(y=audio, sr=sample_rate)
    spectral_contrast_scaled = np.mean(spectral_contrast.T, axis=0)
    
    zero_crossing_rate = librosa.feature.zero_crossing_rate(audio)
    zero_crossing_rate_scaled = np.mean(zero_crossing_rate.T, axis=0)
    
    features = np.concatenate([mfccs_features_scaled, mel_spectrogram_scaled, spectral_contrast_scaled, zero_crossing_rate_scaled])
    return features

# 훈련 데이터 처리
for index, row in tqdm(train_df.iterrows(), total=len(train_df)):
    file_path = row['path']  # CSV 파일의 경로 열 이름에 맞게 조정
    label = row['label']  # CSV 파일의 레이블 열 이름에 맞게 조정
    features = extract_features(file_path)
    data.append(features)
    labels.append(label)

# Unlabeled 데이터 처리
unlabeled_data_dir = 'unlabeled_data'
for root, dirs, files in os.walk(unlabeled_data_dir):
    for file in files:
        file_path = os.path.join(root, file)
        features = extract_features(file_path)
        data.append(features)
        labels.append('unknown')  # 레이블 없는 데이터

# Feature DataFrame 생성
feature_df = pd.DataFrame({"features": data, "class": labels})

# 레이블 인코딩
def label_encoder(column):
    le = LabelEncoder().fit(column)
    print(column.name, le.classes_)
    return le.transform(column)

feature_df["class"] = label_encoder(feature_df["class"])

X = np.array(feature_df["features"].tolist())
y = np.array(feature_df["class"].tolist())

# 데이터 균형 맞추기
ros = RandomOverSampler(random_state=42)
X_resampled, y_resampled = ros.fit_resample(X, y)

y_resampled = to_categorical(y_resampled)

X_train, X_val, y_train, y_val = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

num_labels = len(feature_df["class"].unique())

input_shape = (X.shape[1],)

# Residual Block 정의
def residual_block(x, units):
    shortcut = x
    x = Dense(units)(x)
    x = Activation('relu')(x)
    x = Dropout(0.5)(x)
    x = Dense(units)(x)
    x = Add()([x, shortcut])
    x = Activation('relu')(x)
    x = Dropout(0.5)(x)
    return x

# 모델 생성
input_layer = Input(shape=input_shape)
x = Dense(128)(input_layer)
x = Activation('relu')(x)
x = Dropout(0.5)(x)

# Residual Blocks
x = residual_block(x, 128)
x = residual_block(x, 128)

# 2D to 3D 텐서로 변환
x = Reshape((x.shape[1], 1))(x)

# Attention Mechanism
attention = Attention()([x, x])
x = Add()([x, attention])
x = Reshape((x.shape[1],))(x)  # 3D 텐서를 2D로 변환

x = Dense(256)(x)
x = Activation('relu')(x)
x = Dropout(0.5)(x)
x = Dense(128)(x)
x = Activation('relu')(x)
x = Dropout(0.5)(x)
output_layer = Dense(num_labels, activation='softmax')(x)

model = Model(inputs=input_layer, outputs=output_layer)

model.compile(loss="categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

model.summary()

early = EarlyStopping(monitor="val_loss", patience=5)

history = model.fit(X_train, y_train, validation_data=(X_val, y_val), batch_size=64, epochs=100, callbacks=[early])

val_loss, val_acc = model.evaluate(X_val, y_val)
print("Validation Loss:", val_loss)
print("Validation Accuracy:", val_acc)

# 테스트 데이터 예측 및 제출 파일 생성
def detect_fake(filename):
    features = extract_features(filename)
    features = features.reshape(1, -1)
    result_array = model.predict(features)
    
    if result_array.shape[1] != 2:
        print("Warning: Unexpected result array shape")
        return "UNKNOWN"

    result_classes = ["FAKE", "REAL"]
    result = np.argmax(result_array[0])
    
    return result_classes[result]

# 예측 함수를 사용하여 각 파일에 대한 예측 결과 리스트 생성
predictions = []
for index, row in tqdm(test_df.iterrows(), total=len(test_df)):
    file_path = row['path']  # CSV 파일의 경로 열 이름에 맞게 조정
    prediction = detect_fake(file_path)
    predictions.append(prediction)

# 예측 결과를 DataFrame으로 만들어 CSV 파일로 저장
submit = pd.read_csv('./sample_submission.csv')
submit.iloc[:, 1] = predictions
submit.to_csv('./sg_submit5.csv', index=False)

# sg_submit5.csv 파일이 생성되었음을 알림
print("sg_submit5.csv 파일이 생성되었습니다.")


100%|██████████| 55438/55438 [55:08<00:00, 16.76it/s]  


class ['fake' 'real' 'unknown']


Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_1       │ (None, 176)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_8 (Dense)     │ (None, 128)       │     22,656 │ input_layer_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_7        │ (None, 128)       │          0 │ dense_8[0][0]     │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_7 (Dropout) │ (None, 128)       │          0 │ activation_7[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_9 (Dense)     │ (None, 128)       │     16,512 │ dropout_7[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_8        │ (None, 128)       │          0 │ dense_9[0][0]     │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_8 (Dropout) │ (None, 128)       │          0 │ activation_8[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_10 (Dense)    │ (None, 128)       │     16,512 │ dropout_8[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_3 (Add)         │ (None, 128)       │          0 │ dense_10[0][0],   │
│                     │                   │            │ dropout_7[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_9        │ (None, 128)       │          0 │ add_3[0][0]       │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_9 (Dropout) │ (None, 128)       │          0 │ activation_9[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_11 (Dense)    │ (None, 128)       │     16,512 │ dropout_9[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_10       │ (None, 128)       │          0 │ dense_11[0][0]    │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_10          │ (None, 128)       │          0 │ activation_10[0]… │
│ (Dropout)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_12 (Dense)    │ (None, 128)       │     16,512 │ dropout_10[0][0]  │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_4 (Add)         │ (None, 128)       │          0 │ dense_12[0][0],   │
│                     │                   │            │ dropout_9[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_11       │ (None, 128)       │          0 │ add_4[0][0]       │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_11          │ (None, 128)       │          0 │ activation_11[0]… │
│ (Dropout)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ reshape (Reshape)   │ (None, 128, 1)    │          0 │ dropout_11[0][0]  │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ attention_1         │ (None, 128, 1)    │          0 │ reshape[0][0],  

 Total params: 155,011 (605.51 KB)

...

Epoch 1/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 16s 9ms/step - accuracy: 0.3375 - loss: 48.3066 - val_accuracy: 0.3318 - val_loss: 1.0987
Epoch 2/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 9s 8ms/step - accuracy: 0.3324 - loss: 1.1665 - val_accuracy: 0.3323 - val_loss: 1.0986
Epoch 3/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 9s 9ms/step - accuracy: 0.3335 - loss: 1.1152 - val_accuracy: 0.3318 - val_loss: 1.0988
Epoch 4/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 11s 10ms/step - accuracy: 0.3325 - loss: 1.1073 - val_accuracy: 0.3323 - val_loss: 1.0986
Epoch 5/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 10s 10ms/step - accuracy: 0.3334 - loss: 1.1012 - val_accuracy: 0.3323 - val_loss: 1.0987
Epoch 6/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 11s 10ms/step - accuracy: 0.3352 - loss: 1.1014 - val_accuracy: 0.3318 - val_loss: 1.0987
Epoch 7/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 10s 10ms/step - accuracy: 0.3346 - loss: 1.1011 - val_accuracy: 0.3318 - val_loss: 1.0987
522/522 ━━━━━━━━━━━━━━━━━━━━ 2s 3ms/step - accuracy: 0.3345 - loss: 1.098

  0%|          | 0/50000 [00:00<?, ?it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 150ms/step


  0%|          | 0/50000 [00:00<?, ?it/s]


IndexError: list index out of range

In [2]:
import numpy as np
import pandas as pd
import os
import librosa
from tqdm import tqdm
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from imblearn.over_sampling import RandomOverSampler
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Activation, Dropout, Add, BatchNormalization, Reshape, Attention
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam

# CSV 파일에서 오디오 파일 경로 및 레이블 읽기
train_df = pd.read_csv('train.csv')
test_df = pd.read_csv('test.csv')

data = []
labels = []

# 특징 추출 함수
def extract_features(file_path):
    audio, sample_rate = librosa.load(file_path, res_type="kaiser_fast")
    mfccs_features = librosa.feature.mfcc(y=audio, sr=sample_rate, n_mfcc=40)
    mfccs_features_scaled = np.mean(mfccs_features.T, axis=0)
    
    mel_spectrogram = librosa.feature.melspectrogram(y=audio, sr=sample_rate)
    mel_spectrogram_db = librosa.power_to_db(mel_spectrogram, ref=np.max)
    mel_spectrogram_scaled = np.mean(mel_spectrogram_db.T, axis=0)
    
    spectral_contrast = librosa.feature.spectral_contrast(y=audio, sr=sample_rate)
    spectral_contrast_scaled = np.mean(spectral_contrast.T, axis=0)
    
    zero_crossing_rate = librosa.feature.zero_crossing_rate(audio)
    zero_crossing_rate_scaled = np.mean(zero_crossing_rate.T, axis=0)
    
    features = np.concatenate([mfccs_features_scaled, mel_spectrogram_scaled, spectral_contrast_scaled, zero_crossing_rate_scaled])
    return features

# 훈련 데이터 처리
for index, row in tqdm(train_df.iterrows(), total=len(train_df)):
    file_path = row['path']
    label = row['label']
    features = extract_features(file_path)
    data.append(features)
    labels.append(label)

# Unlabeled 데이터 처리
unlabeled_data_dir = 'unlabeled_data'
for root, dirs, files in os.walk(unlabeled_data_dir):
    for file in files:
        file_path = os.path.join(root, file)
        features = extract_features(file_path)
        data.append(features)
        labels.append('unknown')

# Feature DataFrame 생성
feature_df = pd.DataFrame({"features": data, "class": labels})

# 레이블 인코딩
def label_encoder(column):
    le = LabelEncoder().fit(column)
    print(column.name, le.classes_)
    return le.transform(column)

feature_df["class"] = label_encoder(feature_df["class"])

X = np.array(feature_df["features"].tolist())
y = np.array(feature_df["class"].tolist())

# 데이터 균형 맞추기
ros = RandomOverSampler(random_state=42)
X_resampled, y_resampled = ros.fit_resample(X, y)

y_resampled = to_categorical(y_resampled)

X_train, X_val, y_train, y_val = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

num_labels = y_resampled.shape[1]

input_shape = (X.shape[1],)

# 모델 생성
input_layer = Input(shape=input_shape)
x = Dense(128)(input_layer)
x = Activation('relu')(x)
x = Dropout(0.5)(x)

# Residual Blocks
def residual_block(x, units):
    shortcut = x
    x = Dense(units)(x)
    x = BatchNormalization()(x)
    x = Activation('relu')(x)
    x = Dropout(0.5)(x)
    x = Dense(units)(x)
    x = BatchNormalization()(x)
    x = Add()([x, shortcut])
    x = Activation('relu')(x)
    x = Dropout(0.5)(x)
    return x

x = residual_block(x, 128)
x = residual_block(x, 128)

# Attention Mechanism
# 2D to 3D 텐서로 변환
x = Reshape((x.shape[1], 1))(x)
attention = Attention()([x, x])
x = Add()([x, attention])
# 3D 텐서를 다시 2D 텐서로 변환
x = Reshape((x.shape[1],))(x)

x = Dense(256)(x)
x = Activation('relu')(x)
x = Dropout(0.5)(x)
x = Dense(128)(x)
x = Activation('relu')(x)
x = Dropout(0.5)(x)
output_layer = Dense(num_labels, activation='softmax')(x)

model = Model(inputs=input_layer, outputs=output_layer)

# 옵티마이저 변경
optimizer = Adam(learning_rate=1e-4)

model.compile(loss="categorical_crossentropy", optimizer=optimizer, metrics=["accuracy"])

model.summary()

early = EarlyStopping(monitor="val_loss", patience=5)

history = model.fit(X_train, y_train, validation_data=(X_val, y_val), batch_size=64, epochs=100, callbacks=[early])

val_loss, val_acc = model.evaluate(X_val, y_val)
print("Validation Loss:", val_loss)
print("Validation Accuracy:", val_acc)

# 테스트 데이터 예측 및 제출 파일 생성
def detect_fake(filename):
    features = extract_features(filename)
    features = features.reshape(1, -1)
    result_array = model.predict(features)
    
    if result_array.shape[1] != num_labels:
        print("Warning: Unexpected result array shape")
        return "UNKNOWN"

    result_classes = ["FAKE", "REAL"]
    result = np.argmax(result_array[0])
    
    return result_classes[result]

# 예측 함수를 사용하여 각 파일에 대한 예측 결과 리스트 생성
predictions = []
for index, row in tqdm(test_df.iterrows(), total=len(test_df)):
    file_path = row['path']
    prediction = detect_fake(file_path)
    predictions.append(prediction)

# 예측 결과를 DataFrame으로 만들어 CSV 파일로 저장
submit = pd.read_csv('./sample_submission.csv')
submit.iloc[:, 1] = predictions
submit.to_csv('./sg_submit6.csv', index=False)

# sg_submit6.csv 파일이 생성되었음을 알림
print("sg_submit6.csv 파일이 생성되었습니다.")


100%|██████████| 55438/55438 [42:26<00:00, 21.77it/s]  


class ['fake' 'real' 'unknown']


Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_1       │ (None, 176)       │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_8 (Dense)     │ (None, 128)       │     22,656 │ input_layer_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_7        │ (None, 128)       │          0 │ dense_8[0][0]     │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_7 (Dropout) │ (None, 128)       │          0 │ activation_7[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_9 (Dense)     │ (None, 128)       │     16,512 │ dropout_7[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 128)       │        512 │ dense_9[0][0]     │
│ (BatchNormalizatio… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_8        │ (None, 128)       │          0 │ batch_normalizat… │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_8 (Dropout) │ (None, 128)       │          0 │ activation_8[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_10 (Dense)    │ (None, 128)       │     16,512 │ dropout_8[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 128)       │        512 │ dense_10[0][0]    │
│ (BatchNormalizatio… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ add_3 (Add)         │ (None, 128)       │          0 │ batch_normalizat… │
│                     │                   │            │ dropout_7[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_9        │ (None, 128)       │          0 │ add_3[0][0]       │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_9 (Dropout) │ (None, 128)       │          0 │ activation_9[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_11 (Dense)    │ (None, 128)       │     16,512 │ dropout_9[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 128)       │        512 │ dense_11[0][0]    │
│ (BatchNormalizatio… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_10       │ (None, 128)       │          0 │ batch_normalizat… │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout_10          │ (None, 128)       │          0 │ activation_10[0]… │
│ (Dropout)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_12 (Dense)    │ (None, 128)       │     16,512 │ dropout_10[0][0]  │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 128)       │        512 │ dense_12[0][0]    │
│ (BatchNormalizatio… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼─────────────────

 Total params: 157,059 (613.51 KB)

...

Epoch 1/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 13s 8ms/step - accuracy: 0.3312 - loss: 230.3165 - val_accuracy: 0.3558 - val_loss: 1.2132
Epoch 2/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 8s 8ms/step - accuracy: 0.3347 - loss: 23.6359 - val_accuracy: 0.3359 - val_loss: 1.0992
Epoch 3/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 8s 8ms/step - accuracy: 0.3298 - loss: 4.3722 - val_accuracy: 0.3359 - val_loss: 1.0993
Epoch 4/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 8s 8ms/step - accuracy: 0.3360 - loss: 1.8809 - val_accuracy: 0.3359 - val_loss: 1.0990
Epoch 5/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 9s 8ms/step - accuracy: 0.3278 - loss: 1.4237 - val_accuracy: 0.3359 - val_loss: 1.0988
Epoch 6/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 10s 9ms/step - accuracy: 0.3317 - loss: 1.2124 - val_accuracy: 0.3318 - val_loss: 1.0987
Epoch 7/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 8s 8ms/step - accuracy: 0.3307 - loss: 1.1814 - val_accuracy: 0.3318 - val_loss: 1.0987
Epoch 8/100
1044/1044 ━━━━━━━━━━━━━━━━━━━━ 8s 8ms/step - accuracy: 0.3380 - lo

  0%|          | 0/50000 [00:00<?, ?it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 167ms/step


  0%|          | 0/50000 [00:00<?, ?it/s]


IndexError: list index out of range